# Clustering Mexico neighborhoods by their venues and the total number of them 

### Importing libraries 

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library


print('Libraries imported.')

Libraries imported.


## 1.- Get and prepare the data

### Read csv file which contains Mexico city neighborhoods and their coordinates 

In [4]:
neighborhoods = pd.read_csv('coloniascdmx.csv')
print(neighborhoods.shape)
neighborhoods.head()

(1812, 9)


COLONIA  ENTIDAD  \
0                              IRRIGACION      9.0   
1                 MARINA NACIONAL (U HAB)      9.0   
2              PEDREGAL DE STO DOMINGO VI      9.0   
3  VILLA PANAMERICANA 7MA. SECCIN (U HAB)      9.0   
4  VILLA PANAMERICANA 6TA. SECCIN (U HAB)      9.0   

                      Geo Point  \
0  19.4429549298,-99.2099357048   
1  19.4466319056,-99.1795110575   
2  19.3234027183,-99.1654676133   
3   19.304604269,-99.1677617231   
4  19.3112238873,-99.1696478642   

                                           Geo Shape  CVE_ALC        ALCALDIA  \
0  {"type": "Polygon", "coordinates": [[[-99.2115...       16  MIGUEL HIDALGO   
1  {"type": "Polygon", "coordinates": [[[-99.1797...       16  MIGUEL HIDALGO   
2  {"type": "Polygon", "coordinates": [[[-99.1622...        3        COYOACAN   
3  {"type": "Polygon", "coordinates": [[[-99.1676...        3        COYOACAN   
4  {"type": "Polygon", "coordinates": [[[-99.1702...        3        COYOACAN   

  CVE_COL                      SECC_COM    SECC_PAR  
0  16-035        5079, 5080, 5083, 5102  5068, 5082  
1  16-049                    5137, 5182         NaN  
2  03-144  381, 394, 494, 416, 417, 439         NaN  
3  03-121                           NaN    474, 475  
4  03-120                           NaN         458

### Droping unnecesary columns

In [5]:
neighborhoods.drop(['ENTIDAD','Geo Shape', 'CVE_ALC', 'CVE_COL', 'SECC_COM', 'SECC_PAR'], axis=1, inplace = True)
print(neighborhoods.shape)
neighborhoods.head()

(1812, 3)


COLONIA                     Geo Point  \
0                              IRRIGACION  19.4429549298,-99.2099357048   
1                 MARINA NACIONAL (U HAB)  19.4466319056,-99.1795110575   
2              PEDREGAL DE STO DOMINGO VI  19.3234027183,-99.1654676133   
3  VILLA PANAMERICANA 7MA. SECCIN (U HAB)   19.304604269,-99.1677617231   
4  VILLA PANAMERICANA 6TA. SECCIN (U HAB)  19.3112238873,-99.1696478642   

         ALCALDIA  
0  MIGUEL HIDALGO  
1  MIGUEL HIDALGO  
2        COYOACAN  
3        COYOACAN  
4        COYOACAN

### Split the geo point colum to obtain lat and long

In [7]:
df_aux= neighborhoods['Geo Point'].str.split(',',expand=True)
print(df_aux.shape)
df_aux.head()

(1812, 2)


0               1
0  19.4429549298  -99.2099357048
1  19.4466319056  -99.1795110575
2  19.3234027183  -99.1654676133
3   19.304604269  -99.1677617231
4  19.3112238873  -99.1696478642

### Dropping Geo Point and mergin the 2 dataframes

In [10]:
df_aux.rename(columns={0:'Latitude', 1:'Longitude'}, inplace= True)
print(df_aux.shape)
df_aux.head()

(1812, 2)


Latitude       Longitude
0  19.4429549298  -99.2099357048
1  19.4466319056  -99.1795110575
2  19.3234027183  -99.1654676133
3   19.304604269  -99.1677617231
4  19.3112238873  -99.1696478642

In [11]:
#drop Geo Point
neighborhoods.drop(['Geo Point'], axis=1, inplace=True)

In [12]:
print(neighborhoods.shape)
neighborhoods.head()

(1812, 2)


COLONIA        ALCALDIA
0                              IRRIGACION  MIGUEL HIDALGO
1                 MARINA NACIONAL (U HAB)  MIGUEL HIDALGO
2              PEDREGAL DE STO DOMINGO VI        COYOACAN
3  VILLA PANAMERICANA 7MA. SECCIN (U HAB)        COYOACAN
4  VILLA PANAMERICANA 6TA. SECCIN (U HAB)        COYOACAN

In [14]:
neighborhoods['Latitude']=df_aux['Latitude']
print(neighborhoods.shape)
neighborhoods.head()

(1812, 3)


COLONIA        ALCALDIA       Latitude
0                              IRRIGACION  MIGUEL HIDALGO  19.4429549298
1                 MARINA NACIONAL (U HAB)  MIGUEL HIDALGO  19.4466319056
2              PEDREGAL DE STO DOMINGO VI        COYOACAN  19.3234027183
3  VILLA PANAMERICANA 7MA. SECCIN (U HAB)        COYOACAN   19.304604269
4  VILLA PANAMERICANA 6TA. SECCIN (U HAB)        COYOACAN  19.3112238873

In [15]:
neighborhoods['Longitude']=df_aux['Longitude']
print(neighborhoods.shape)
neighborhoods.head()

(1812, 4)


COLONIA        ALCALDIA       Latitude  \
0                              IRRIGACION  MIGUEL HIDALGO  19.4429549298   
1                 MARINA NACIONAL (U HAB)  MIGUEL HIDALGO  19.4466319056   
2              PEDREGAL DE STO DOMINGO VI        COYOACAN  19.3234027183   
3  VILLA PANAMERICANA 7MA. SECCIN (U HAB)        COYOACAN   19.304604269   
4  VILLA PANAMERICANA 6TA. SECCIN (U HAB)        COYOACAN  19.3112238873   

        Longitude  
0  -99.2099357048  
1  -99.1795110575  
2  -99.1654676133  
3  -99.1677617231  
4  -99.1696478642

In [18]:
#Checking if there are NaN values 
neighborhoods.isna().any(axis= None)

True

In [19]:
#Checking which columns have NaN values
neighborhoods.isna().any()

COLONIA      False
ALCALDIA     False
Latitude      True
Longitude     True
dtype: bool

In [21]:
#Determining how many NaN values exist
neighborhoods.isna().T.any().T.sum()

4

There are four rows with nan values, we may proceed to drop those rows 

In [28]:
neighborhoods.dropna(inplace=True)
print(neighborhoods.shape)
neighborhoods.head()

(1808, 4)


COLONIA        ALCALDIA       Latitude  \
0                              IRRIGACION  MIGUEL HIDALGO  19.4429549298   
1                 MARINA NACIONAL (U HAB)  MIGUEL HIDALGO  19.4466319056   
2              PEDREGAL DE STO DOMINGO VI        COYOACAN  19.3234027183   
3  VILLA PANAMERICANA 7MA. SECCIN (U HAB)        COYOACAN   19.304604269   
4  VILLA PANAMERICANA 6TA. SECCIN (U HAB)        COYOACAN  19.3112238873   

        Longitude  
0  -99.2099357048  
1  -99.1795110575  
2  -99.1654676133  
3  -99.1677617231  
4  -99.1696478642

In [29]:
#Checking which columns have NaN values
neighborhoods.isna().any()

COLONIA      False
ALCALDIA     False
Latitude     False
Longitude    False
dtype: bool

 Finally there are 1808 neighborhoods which we may proceed to get their venues  

### Eliminating some rows 

In order to delete information which are not relevant for our purpose we are gonna delete neighborhoods that already are  habitational complexes, Those neighborhoods include the string (U HAB) on their names. 

In [74]:
aux=neighborhoods[neighborhoods['COLONIA'].str.contains('(U HAB)', regex=False)]
print(aux.shape)
aux.head()

(253, 4)


COLONIA             ALCALDIA  \
1                  MARINA NACIONAL (U HAB)       MIGUEL HIDALGO   
3   VILLA PANAMERICANA 7MA. SECCIN (U HAB)             COYOACAN   
4   VILLA PANAMERICANA 6TA. SECCIN (U HAB)             COYOACAN   
12                           BAHIA (U HAB)  VENUSTIANO CARRANZA   
24                PEMEX LINDAVISTA (U HAB)    GUSTAVO A. MADERO   

         Latitude       Longitude  
1   19.4466319056  -99.1795110575  
3    19.304604269  -99.1677617231  
4   19.3112238873  -99.1696478642  
12  19.4164746958  -99.0833041984  
24  19.5063694916  -99.1340096017

There are 253 neighborhoods which already are housing developments, we are gonna delete those rows

In [75]:
neighborhoods.drop(neighborhoods[neighborhoods['COLONIA'].str.contains('(U HAB)', regex=False)].index, inplace=True)
print(neighborhoods.shape)
neighborhoods.head()

(1555, 4)


COLONIA             ALCALDIA       Latitude  \
0                  IRRIGACION       MIGUEL HIDALGO  19.4429549298   
2  PEDREGAL DE STO DOMINGO VI             COYOACAN  19.3234027183   
5         SANTA CRUZ AVIACION  VENUSTIANO CARRANZA  19.4223039522   
6          MAGDALENA  MIXHUCA  VENUSTIANO CARRANZA   19.407130147   
7         COPILCO UNIVERSIDAD             COYOACAN  19.3361172512   

        Longitude  
0  -99.2099357048  
2  -99.1654676133  
5  -99.0972147602  
6  -99.1181313602  
7  -99.1826102146

### Use geopy to get coordinates from Toronto

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>mex_explorer</em>, as shown below.


In [76]:
#Mexico city coordinates 
latitude = 19.4978
longitude = -99.1269
print('The geograpical coordinate of Mexico city are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Mexico city are 19.4978, -99.1269.


### Create a map of Toronto with neighborhoods superimposed

In [77]:
# create map of Toronto using latitude and longitude values
map_Mex = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['ALCALDIA'], neighborhoods['COLONIA']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Mex)  
    
map_Mex

In [78]:
neighborhoods['ALCALDIA'].value_counts()

ALVARO OBREGON            230
IZTAPALAPA                225
GUSTAVO A. MADERO         178
TLALPAN                   159
COYOACAN                  114
AZCAPOTZALCO               86
MIGUEL HIDALGO             85
VENUSTIANO CARRANZA        74
XOCHIMILCO                 72
BENITO JUAREZ              63
CUAUHTEMOC                 59
TLAHUAC                    56
IZTACALCO                  53
LA MAGDALENA CONTRERAS     48
CUAJIMALPA DE MORELOS      42
MILPA ALTA                 11
Name: ALCALDIA, dtype: int64

### Get data from Foursquare

#### Define Foursquare credentials

In [96]:
CLIENT_ID = 'CKR3UDPNSLNLPFBNO11BLZXTVY5YML5PPTS3Y0Z2YGEBDNTX' # your Foursquare ID
CLIENT_SECRET = 'UWTHEZWYMRZ2RTEAMPYMS1FIJUXKKCNMMN3I4SBVJ0DHSLP3' # your Foursquare Secret
VERSION = '20201504' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: CKR3UDPNSLNLPFBNO11BLZXTVY5YML5PPTS3Y0Z2YGEBDNTX
CLIENT_SECRET:UWTHEZWYMRZ2RTEAMPYMS1FIJUXKKCNMMN3I4SBVJ0DHSLP3


## 2. Explore Neighborhoods in Mexico city

In [80]:
# defining radius and limit of venues to get
radius=1000 #meters
LIMIT=100

In [81]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [87]:
print(lat,lng)

19.4215844077 -99.1053538347


In [99]:
mex_venues = getNearbyVenues(names=neighborhoods['COLONIA'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

IRRIGACION
PEDREGAL DE STO DOMINGO VI
SANTA CRUZ AVIACION
MAGDALENA  MIXHUCA
COPILCO UNIVERSIDAD
MORALES SECCION ALAMEDA (POLANCO)
AJUSCO HUAYAMILPAS
CHIMALISTAC
EL ARENAL PTO AEREO (FRACC)
CUADRANTE DE SAN FRANCISCO
EL RELOJ
EL MIRADOR
LOS CIPRESES
LOS CEDROS (FRACC)
CONSTITUCION DE LA REPUBLICA
CASTILLO GRANDE (AMPL)
7 DE NOVIEMBRE
INDUSTRIAL I
TEPETATAL
SAN PEDRO EL CHICO
GUADALUPE TEPEYAC
GUADALUPE VICTORIA II
LA MALINCHE
EX-ESCUELA DE TIRO
GRACIANO SANCHEZ
INDUSTRIAL II
SAN FELIPE DE JESUS I
LA MAGDALENA PETLACALCO (PBLO)
JUVENTUD UNIDA
TLALPAN CENTRO
TLALMILLE
VERGEL DE COYOACAN-VERGEL DEL SUR
VILLA LAZARO CARDENAS
VERANO
TIERRA NUEVA
REAL DEL SUR-VILLAS DEL SUR-RESIDENCIAL ACOXPA
SAN FRANCISCO TECOXPA (PBLO)
SAN AGUSTIN OHTENCO (PBLO)
ZONA ESCOLAR I
AMSA
CALTONGO (BARR)
LA CONCHA
ARENAL PUERTA TEPEPAN
FRACCIONAMIENTO COYUYA
SANTIAGO AHUIZOTLA (PBLO)
TIERRA NUEVA
SAN FRANCISCO TETECALA (PBLO)
TRABAJADORES DEL HIERRO
ATLAMPA
ASTURIAS (AMPL)
TEZONTITLA-ZOMPANTITLA
SAN PEDRO TLAHUAC

SAN ANTONIO (FRACC)
SAN RAFAEL
NUEVA ESPAA
POTRERO DEL LLANO
SAN SALVADOR XOCHIMANCA
MONTE ALTO
SAN PEDRO XALPA (AMPL) II
HACIENDA DE GUADALUPE CHIMALISTAC
PRO HOGAR II
LOMAS DE SAN LORENZO II
DESARROLLO URBANO QUETZALCOATL  I
SANTA MARIA AZTAHUACAN (EJ) II
XALPA I
AMADO NERVO
JUAN ESCUTIA I
SAN JUAN XALPA I
CONSTITUCION DE 1917 I
CERRO DE LA ESTRELLA II
9 1/2 - FRANCISCO VILLA (EJERCITO CONSTITUCIONALISTA) (CONJ HAB)
PARAISO
SAN ANTONIO (BARR)
MIRAVALLE
LA PLANTA
LOMAS ESTRELLA 1A SECC (FRACC)
MEXICALTZINGO (PBLO)
JACARANDAS
ESCUADRON 201
JESUS DEL MONTE
LOMAS DE SAN BERNABE (AMPL)
PUEBLO NUEVO BAJO
PLAZUELA DEL PEDREGAL
ACTIPAN
EL SANTUARIO (AMPL)
CACAMA
EL EDEN
EJTO CONSTITUCIONALISTA, SUPERMANZANA II ( U HAB)
GRANADA
VALLE GOMEZ
PUEBLA
MICHOACANA (AMPL)
TRES MOSQUETEROS
POPOTLA II
COUNTRY CLUB
EL CARACOL
EX EJIDO SAN FRANCISCO CULHUACAN I
EL PARQUE DE COYOACAN (FRACC)
SAN MATEO (BARR)
SANTA URSULA COYOACAN
AVIACION CIVIL (AMPL)
ADOLFO RUIZ CORTINES II
EL ARENAL 1A SECCION
AERONAUTI

LA VENTA
HUAYATLA
ATACAXCO
LAS CRUCES
LOMAS DE SAN BERNABE
INDEPENDENCIA
INSURGENTES MIXCOAC
SANTIAGO ACAHUALTEPEC (PBLO)
SANTA MARIA TOMATLAN (AMPL)
SIERRA DEL VALLE
SANTA MARIA TOMATLAN
8A DE SAN MIGUEL (AMPL)
PRESIDENTES DE MEXICO
SAN PABLO I, II Y V-LOMAS DEL PARAISO
LOS REYES (AMPL)
GUADALUPE DEL MORAL
EL RETOO
GRANJAS ESTRELLA I
BARRANCAS DE GUADALUPE
EJTO CONSTITUCIONALISTA II ( U HAB)
AMERICA
FRANCISCO I MADERO
LOMAS DE BARRILACO (LOMAS DE CHAPULTEPEC)
MORALES SECCION PALMAS (POLANCO)
PENSIL NORTE
PENSIL SAN JUANICO
RINCON DEL BOSQUE
TLAXPANA
DEL CARMEN
HERMOSILLO
LOS ROBLES (FRACC)
NUEVA DIAZ ORDAZ
PEDREGAL DE LA ZORRA
PEDREGAL DEL MAUREL
SAN LUCAS (BARR)
SANTA CECILIA
PEDREGAL DE STO DOMINGO VII
ROMERO DE TERREROS (COND)
PENITENCIARIA (AMPL)
MOCTEZUMA 2A SECCION III
NAPOLES
C T M ARAGON AMPLIACION (U)
GABRIEL HERNANDEZ
ESTANZUELA
PANAMERICANA
VILLA MILPA ALTA (PBLO)
SAN BARTOLOME XICOMULCO (PBLO)
VILLA DE ARAGON
PEDREGAL DE SN NICOLAS 1A SECC
PEDREGAL DE SN NICOLAS 3A SECC
RI

EL ARENAL 3A SECCION
EL ARENAL 4A SECCION
JARDIN BALBUENA II
DE LA CANDELARIA (PBLO)
EX HACIENDA COAPA
LA MAGDALENA CULHUACAN (BARR)
LA LOMA
LIBERACION PROLETARIA
LOPEZ PORTILLO
SAN JUAN IXTAYOPAN (PBLO)
JAIME TORRES BODET
LA CONCHITA II
SAN JOSE
MIGUEL HIDALGO OTE
SAN MIGUEL
PANTITLAN I
CAMPAMENTO 2 DE OCTUBRE I
JUVENTINO ROSAS II
PANTITLAN II
SANTIAGO NORTE
EUZKADI
PRADOS DEL ROSARIO
LIBERACION
SANTA MARIA MALINALCO (PBLO)
CALZADA JALALPA
EL ARBOL
OLIVAR DE LOS PADRES
MILPA DEL CEDRO
GOLONDRINAS
EMANCIPACION DEL PUEBLO
PALMAS
SAN ANGEL INN
PUENTE COLORADO
1RA VICTORIA SECCION BOSQUES
GUERRERO II
VISTA ALEGRE
MORELOS II
FELIPE PESCADOR
BONDOJITO
CUCHILLA LA JOYA
LA SANTISIMA (BARR)
CLUB DE GOLF MEXICO-SAN BUENAVENTURA
CUCHILLA DE PADIERNA
LOMAS DE CUILOTEPEC
PEDREGAL DE SN NICOLAS 2A SECC
ROMULO SANCHEZ-SAN FERNANDO (BARR)-PEA POBRE
SN JUAN TEPEXIMILPA
ZACATIENDA
SAN LORENZO
VALLEJO PONIENTE
PROVIDENCIA II
LA CANDELARIA TICOMAN (BARR)
HEROES DE CHAPULTEPEC
EL CONTADERO
EL TIANGUILLO
L

### Let's check the size of the resulting frame

In [100]:
print(mex_venues.shape)
mex_venues.head()

(34388, 7)


Neighborhood Neighborhood Latitude Neighborhood Longitude  \
0   IRRIGACION         19.4429549298         -99.2099357048   
1   IRRIGACION         19.4429549298         -99.2099357048   
2   IRRIGACION         19.4429549298         -99.2099357048   
3   IRRIGACION         19.4429549298         -99.2099357048   
4   IRRIGACION         19.4429549298         -99.2099357048   

                       Venue  Venue Latitude  Venue Longitude  Venue Category  
0          La Pantera Fresca       19.442104       -99.209314  Ice Cream Shop  
1         Glorieta de Fátima       19.444397       -99.210792            Park  
2                     Panmex       19.440615       -99.208584          Bakery  
3           Canchas de Tenis       19.440700       -99.211627    Tennis Court  
4  Salchichonería San Miguel       19.440234       -99.207833   Deli / Bodega

### Saving the dataframe 

In [101]:
mex_venues.to_csv('mex_venues.csv')

#### Let's find out how many unique categories can be curated from all the returned venues

In [105]:
print('There are {} uniques categories.'.format(len(mex_venues['Venue Category'].unique())))

There are 465 uniques categories.


In [113]:
#getting the total number of venues on each neighborhood
aux=pd.DataFrame(mex_venues.groupby(['Neighborhood']).count()['Venue'])
print(type(aux))
print(aux.shape)
aux.head()

<class 'pandas.core.frame.DataFrame'>
(1457, 1)


Venue
Neighborhood           
10 DE ABRIL           7
10 DE MAYO           20
12 DE DICIEMBRE      15
15 DE AGOSTO          5
16 DE SEPTIEMBRE     17

In [115]:
aux.reset_index(inplace=True)
print(type(aux))
print(aux.shape)
aux.head()

<class 'pandas.core.frame.DataFrame'>
(1457, 2)


Neighborhood  Venue
0       10 DE ABRIL      7
1        10 DE MAYO     20
2   12 DE DICIEMBRE     15
3      15 DE AGOSTO      5
4  16 DE SEPTIEMBRE     17

## 3. Analyze Each Neighborhood

In [106]:
# one hot encoding
mex_onehot = pd.get_dummies(mex_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
mex_onehot['Neighborhood'] = mex_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [mex_onehot.columns[-1]] + list(mex_onehot.columns[:-1])
mex_onehot = mex_onehot[fixed_columns]

mex_onehot.head()

Zoo Exhibit  ATM  Accessories Store  Adult Boutique  Advertising Agency  \
0            0    0                  0               0                   0   
1            0    0                  0               0                   0   
2            0    0                  0               0                   0   
3            0    0                  0               0                   0   
4            0    0                  0               0                   0   

   African Restaurant  Airport  Airport Service  American Restaurant  \
0                   0        0                0                    0   
1                   0        0                0                    0   
2                   0        0                0                    0   
3                   0        0                0                    0   
4                   0        0                0                    0   

   Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0             0       0                 0                       0   
1             0       0                 0                       0   
2             0       0                 0                       0   
3             0       0                 0                       0   
4             0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Astrologer  Athletics & Sports  Auditorium  \
0                 0           0                   0           0   
1                 0           0                   0           0   
2                 0           0                   0           0   
3                 0           0                   0           0   
4                 0           0                   0           0   

   Auto Dealership  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0                0            0              0                0          0   
1                0            0              0                0          0   
2                0            0              0                0          0   
3                0            0              0                0          0   
4                0            0              0                0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       1     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bath House  \
0                 0                 0                   0           0   
1                 0                 0                   0           0   
2                 0                 0                   0           0   
3                 0                 0                   0           0   
4                 0                 0                   0           0   

   Bathing Area  Beach  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0             0      0                0         0            0           0   
1             0      0                0         0            0           0   
2             0      0                0         0            0           0   
3             0      0                0         0            0           0   
4             0      0                0         0            0           0   

   Belgian Restaurant  Big Box Store  Bike Rental / Bike Share  Bike Trail  \
0   

In [107]:
mex_onehot.shape

(34388, 465)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [108]:
mex_grouped = mex_onehot.groupby('Neighborhood').mean().reset_index()

As we may observe, there are only 1457 neighborhood, the reason is that when we call for venues using foursquare there wasn't available data from venues near those neighborhoods. This will affect our clustering, we need to add those neighborhoods to our dataframe but first, I think it is important to add a new column to the dataframe which includes the total number of venues near the area. 

## Adding an extra column for the total of venues

In [137]:
#aux values is a dataframe that includes total number of venues for every row we would need to merge it with mex_grouped dataframe
mex_merged= aux
mex_merged= mex_merged.join(mex_grouped.set_index('Neighborhood'), on= 'Neighborhood')
print(mex_merged.shape)
mex_merged.head()


(1457, 466)


Neighborhood  Venue  Zoo Exhibit  ATM  Accessories Store  \
0       10 DE ABRIL      7     0.000000  0.0                0.0   
1        10 DE MAYO     20     0.000000  0.0                0.0   
2   12 DE DICIEMBRE     15     0.066667  0.0                0.0   
3      15 DE AGOSTO      5     0.000000  0.0                0.0   
4  16 DE SEPTIEMBRE     17     0.000000  0.0                0.0   

   Adult Boutique  Advertising Agency  African Restaurant  Airport  \
0             0.0                 0.0                 0.0      0.0   
1             0.0                 0.0                 0.0      0.0   
2             0.0                 0.0                 0.0      0.0   
3             0.0                 0.0                 0.0      0.0   
4             0.0                 0.0                 0.0      0.0   

   Airport Service  American Restaurant  Antique Shop  Arcade  \
0              0.0                  0.0           0.0     0.0   
1              0.0                  0.0           0.0     0.0   
2              0.0                  0.0           0.0     0.0   
3              0.0                  0.0           0.0     0.0   
4              0.0                  0.0           0.0     0.0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0               0.0                     0.0          0.0         0.0   
1               0.0                     0.0          0.0         0.0   
2               0.0                     0.0          0.0         0.0   
3               0.0                     0.0          0.0         0.0   
4               0.0                     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  Astrologer  \
0                  0.0                   0.0               0.0         0.0   
1                  0.1                   0.0               0.0         0.0   
2                  0.0                   0.0               0.0         0.0   
3                  0.0                   0.0               0.0         0.0   
4                  0.0                   0.0               0.0         0.0   

   Athletics & Sports  Auditorium  Auto Dealership  Auto Garage  \
0                 0.0         0.0              0.0          0.0   
1                 0.0         0.0              0.0          0.0   
2                 0.0         0.0              0.0          0.0   
3                 0.0         0.0              0.0          0.0   
4                 0.0         0.0              0.0          0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0            0.0              0.0       0.00         0.0         0.0   
1            0.0              0.0       0.05         0.0         0.0   
2            0.0              0.0       0.00         0.0         0.0   
3            0.0              0.0       0.00         0.0         0.0   
4            0.0              0.0       0.00         0.0         0.0   

     Bakery  Bank       Bar  Baseball Field  Baseball Stadium  \
0  0.000000   0.0  0.000000             0.0               0.0   
1  0.000000   0.0  0.000000             0.0               0.0   
2  0.000000   0.0  0.000000             0.0               0.0   
3  0.000000   0.0  0.000000             0.0               0.0   
4  0.058824   0.0  0.058824             0.0               0.0   

   Basketball Court  Basketball Stadium  Bath House  Bathing Area  Beach  \
0          0.142857                 0.0         0.0           0.0    0.0   
1          0.000000                 0.0         0.0           0.0    0.0   
2          0.000000                 0.0         0.0           0.0    0.0   
3          0.000000                 0.0         0.0           0.0    0.0   
4          0.000000                 0.0         0.0           0.0    0.0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0              0.0       0.0          0.0         0.0                 0.0   
1              0.0       0.0          0.0         0.

In [138]:
mex_merged.rename(columns={'Venue':'Count'}, inplace=True)
print(mex_merged.shape)
mex_merged.head()

(1457, 466)


Neighborhood  Count  Zoo Exhibit  ATM  Accessories Store  \
0       10 DE ABRIL      7     0.000000  0.0                0.0   
1        10 DE MAYO     20     0.000000  0.0                0.0   
2   12 DE DICIEMBRE     15     0.066667  0.0                0.0   
3      15 DE AGOSTO      5     0.000000  0.0                0.0   
4  16 DE SEPTIEMBRE     17     0.000000  0.0                0.0   

   Adult Boutique  Advertising Agency  African Restaurant  Airport  \
0             0.0                 0.0                 0.0      0.0   
1             0.0                 0.0                 0.0      0.0   
2             0.0                 0.0                 0.0      0.0   
3             0.0                 0.0                 0.0      0.0   
4             0.0                 0.0                 0.0      0.0   

   Airport Service  American Restaurant  Antique Shop  Arcade  \
0              0.0                  0.0           0.0     0.0   
1              0.0                  0.0           0.0     0.0   
2              0.0                  0.0           0.0     0.0   
3              0.0                  0.0           0.0     0.0   
4              0.0                  0.0           0.0     0.0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0               0.0                     0.0          0.0         0.0   
1               0.0                     0.0          0.0         0.0   
2               0.0                     0.0          0.0         0.0   
3               0.0                     0.0          0.0         0.0   
4               0.0                     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  Astrologer  \
0                  0.0                   0.0               0.0         0.0   
1                  0.1                   0.0               0.0         0.0   
2                  0.0                   0.0               0.0         0.0   
3                  0.0                   0.0               0.0         0.0   
4                  0.0                   0.0               0.0         0.0   

   Athletics & Sports  Auditorium  Auto Dealership  Auto Garage  \
0                 0.0         0.0              0.0          0.0   
1                 0.0         0.0              0.0          0.0   
2                 0.0         0.0              0.0          0.0   
3                 0.0         0.0              0.0          0.0   
4                 0.0         0.0              0.0          0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0            0.0              0.0       0.00         0.0         0.0   
1            0.0              0.0       0.05         0.0         0.0   
2            0.0              0.0       0.00         0.0         0.0   
3            0.0              0.0       0.00         0.0         0.0   
4            0.0              0.0       0.00         0.0         0.0   

     Bakery  Bank       Bar  Baseball Field  Baseball Stadium  \
0  0.000000   0.0  0.000000             0.0               0.0   
1  0.000000   0.0  0.000000             0.0               0.0   
2  0.000000   0.0  0.000000             0.0               0.0   
3  0.000000   0.0  0.000000             0.0               0.0   
4  0.058824   0.0  0.058824             0.0               0.0   

   Basketball Court  Basketball Stadium  Bath House  Bathing Area  Beach  \
0          0.142857                 0.0         0.0           0.0    0.0   
1          0.000000                 0.0         0.0           0.0    0.0   
2          0.000000                 0.0         0.0           0.0    0.0   
3          0.000000                 0.0         0.0           0.0    0.0   
4          0.000000                 0.0         0.0           0.0    0.0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0              0.0       0.0          0.0         0.0                 0.0   
1              0.0       0.0          0.0         0.

## Adding  extra rows for missed neighborhoods

In [139]:
for name in neighborhoods['COLONIA']: 
    if (name in mex_merged['Neighborhood'].unique()) == False: 
        print(name)
        auxlist=[]
        for i in range(465): 
            if(i==0):
                auxlist.append(name)
                auxlist.append(int(0))
            else: 
                auxlist.append(0.0)
        df_length = len(mex_merged)
        mex_merged.loc[df_length] = auxlist

TEZONTITLA-ZOMPANTITLA
SANTA FE
ALTOS TEPETLICA
EL GAVILLERO
SAN FRANCISCO TLALNEPANTLA (PBLO)
AHUACATITLA
PARAISO SANTA CATARINA
DEGOLLADO CHICO
MALACATES (AMPL)
SAN JOSE OBRERO
SAN LORENZO (BARR)
SAN JUAN TEPENAHUAC (PBLO)
XAXALCO
SAN MIGUEL (AMPL)
QUETZALCOATL 3
LOMAS DE PUERTA GRANDE
JARDINES DE SAN JUAN
EMILIANO ZAPATA 2A
ARBOLEDAS DE CUAUTEPEC (AMPL)
SAN MARCOS (AMPL)
CONDOMINIO DEL BOSQUE (FRACC)-BOSQUE DE TLALPAN
PIEDRA LARGA
SAN PABLO I, II Y V-LOMAS DEL PARAISO
TECACALANCO
SAN FRANCISCO TLALTENCO (PBLO)
SAN MIGUEL TEOTONGO IV
TIERRA COLORADA
3 DE MAYO
HUITZICO-LA POBLANITA
TEOZOMA
SAN JOSE
ATOTOLCO


In [140]:
print(mex_merged.shape)
mex_merged.tail()

(1489, 466)


Neighborhood  Count  Zoo Exhibit  ATM  Accessories Store  \
0       10 DE ABRIL      7     0.000000  0.0                0.0   
1        10 DE MAYO     20     0.000000  0.0                0.0   
2   12 DE DICIEMBRE     15     0.066667  0.0                0.0   
3      15 DE AGOSTO      5     0.000000  0.0                0.0   
4  16 DE SEPTIEMBRE     17     0.000000  0.0                0.0   

   Adult Boutique  Advertising Agency  African Restaurant  Airport  \
0             0.0                 0.0                 0.0      0.0   
1             0.0                 0.0                 0.0      0.0   
2             0.0                 0.0                 0.0      0.0   
3             0.0                 0.0                 0.0      0.0   
4             0.0                 0.0                 0.0      0.0   

   Airport Service  American Restaurant  Antique Shop  Arcade  \
0              0.0                  0.0           0.0     0.0   
1              0.0                  0.0           0.0     0.0   
2              0.0                  0.0           0.0     0.0   
3              0.0                  0.0           0.0     0.0   
4              0.0                  0.0           0.0     0.0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0               0.0                     0.0          0.0         0.0   
1               0.0                     0.0          0.0         0.0   
2               0.0                     0.0          0.0         0.0   
3               0.0                     0.0          0.0         0.0   
4               0.0                     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  Astrologer  \
0                  0.0                   0.0               0.0         0.0   
1                  0.1                   0.0               0.0         0.0   
2                  0.0                   0.0               0.0         0.0   
3                  0.0                   0.0               0.0         0.0   
4                  0.0                   0.0               0.0         0.0   

   Athletics & Sports  Auditorium  Auto Dealership  Auto Garage  \
0                 0.0         0.0              0.0          0.0   
1                 0.0         0.0              0.0          0.0   
2                 0.0         0.0              0.0          0.0   
3                 0.0         0.0              0.0          0.0   
4                 0.0         0.0              0.0          0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0            0.0              0.0       0.00         0.0         0.0   
1            0.0              0.0       0.05         0.0         0.0   
2            0.0              0.0       0.00         0.0         0.0   
3            0.0              0.0       0.00         0.0         0.0   
4            0.0              0.0       0.00         0.0         0.0   

     Bakery  Bank       Bar  Baseball Field  Baseball Stadium  \
0  0.000000   0.0  0.000000             0.0               0.0   
1  0.000000   0.0  0.000000             0.0               0.0   
2  0.000000   0.0  0.000000             0.0               0.0   
3  0.000000   0.0  0.000000             0.0               0.0   
4  0.058824   0.0  0.058824             0.0               0.0   

   Basketball Court  Basketball Stadium  Bath House  Bathing Area  Beach  \
0          0.142857                 0.0         0.0           0.0    0.0   
1          0.000000                 0.0         0.0           0.0    0.0   
2          0.000000                 0.0         0.0           0.0    0.0   
3          0.000000                 0.0         0.0           0.0    0.0   
4          0.000000                 0.0         0.0           0.0    0.0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0              0.0       0.0          0.0         0.0                 0.0   
1              0.0       0.0          0.0         0.

In [132]:
name= '10 DE ABRIL'
if (name in mex_merged['Neighborhood'].unique()) == False: 
    print(name)

it can be observed that We add few rows, the reason is that there a repeated neighborhoods, for this approach we will use the dataset like this 

### Now it is time to cluster the dataset 

In [141]:
# set number of clusters
kclusters = 3

mex_merged_clustering = mex_merged.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(mex_merged_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 0, 2, 0, 0])

In [148]:
# add clustering labels
#mex_merged.insert(0, 'Cluster Labels', kmeans.labels_)

mex_merged2 = neighborhoods
print(mex_merged2.shape)
#delete duplicates 
mex_merged2.drop_duplicates(subset= 'COLONIA', keep='first', inplace=True)
print(mex_merged2.shape)


(1555, 4)
(1489, 4)


In [150]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
mex_merged2.rename(columns={'COLONIA':'Neighborhood'}, inplace=True)
mex_merged2 = mex_merged2.join(mex_merged.set_index('Neighborhood'), on='Neighborhood')
print(mex_merged2.shape )
mex_merged2.head()

(1489, 470)


Neighborhood             ALCALDIA       Latitude  \
0                  IRRIGACION       MIGUEL HIDALGO  19.4429549298   
2  PEDREGAL DE STO DOMINGO VI             COYOACAN  19.3234027183   
5         SANTA CRUZ AVIACION  VENUSTIANO CARRANZA  19.4223039522   
6          MAGDALENA  MIXHUCA  VENUSTIANO CARRANZA   19.407130147   
7         COPILCO UNIVERSIDAD             COYOACAN  19.3361172512   

        Longitude  Cluster Labels  Count  Zoo Exhibit  ATM  Accessories Store  \
0  -99.2099357048               2     42          0.0  0.0                0.0   
2  -99.1654676133               0     19          0.0  0.0                0.0   
5  -99.0972147602               2     36          0.0  0.0                0.0   
6  -99.1181313602               2     28          0.0  0.0                0.0   
7  -99.1826102146               1     73          0.0  0.0                0.0   

   Adult Boutique  Advertising Agency  African Restaurant  Airport  \
0             0.0                 0.0                 0.0      0.0   
2             0.0                 0.0                 0.0      0.0   
5             0.0                 0.0                 0.0      0.0   
6             0.0                 0.0                 0.0      0.0   
7             0.0                 0.0                 0.0      0.0   

   Airport Service  American Restaurant  Antique Shop  Arcade  \
0              0.0                  0.0           0.0     0.0   
2              0.0                  0.0           0.0     0.0   
5              0.0                  0.0           0.0     0.0   
6              0.0                  0.0           0.0     0.0   
7              0.0                  0.0           0.0     0.0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0               0.0                     0.0          0.0         0.0   
2               0.0                     0.0          0.0         0.0   
5               0.0                     0.0          0.0         0.0   
6               0.0                     0.0          0.0         0.0   
7               0.0                     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  Astrologer  \
0                  0.0                   0.0               0.0         0.0   
2                  0.0                   0.0               0.0         0.0   
5                  0.0                   0.0               0.0         0.0   
6                  0.0                   0.0               0.0         0.0   
7                  0.0                   0.0               0.0         0.0   

   Athletics & Sports  Auditorium  Auto Dealership  Auto Garage  \
0            0.000000         0.0              0.0          0.0   
2            0.052632         0.0              0.0          0.0   
5            0.000000         0.0              0.0          0.0   
6            0.035714         0.0              0.0          0.0   
7            0.013699         0.0              0.0          0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0            0.0              0.0   0.000000         0.0         0.0   
2            0.0              0.0   0.000000         0.0         0.0   
5            0.0              0.0   0.027778         0.0         0.0   
6            0.0              0.0   0.000000         0.0         0.0   
7            0.0              0.0   0.027397         0.0         0.0   

     Bakery  Bank       Bar  Baseball Field  Baseball Stadium  \
0  0.023810   0.0  0.000000             0.0               0.0   
2  0.000000   0.0  0.052632             0.0               0.0   
5  0.055556   0.0  0.000000             0.0               0.0   
6  0.000000   0.0  0.000000             0.0               0.0   
7  0.027397   0.0  0.000000             0.0               0.0   

   Basketball Court  Basketball Stadium  Bath House  Bathing Area  Beach  \
0           0.02381                 0.0         0.0           0.0    0.0   
2           0.00000   

In [151]:
mex_merged2['Cluster Labels'].value_counts()

0    897
2    456
1    136
Name: Cluster Labels, dtype: int64

In [154]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(mex_merged2['Latitude'], mex_merged2['Longitude'], mex_merged2['Neighborhood'], mex_merged2['Cluster Labels']):
    #print(cluster)
    label = folium.Popup(str(poi) + ' Cluster ' + str(int(cluster)), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [155]:
print(colors_array)

[[5.00000000e-01 0.00000000e+00 1.00000000e+00 1.00000000e+00]
 [5.03921569e-01 9.99981027e-01 7.04925547e-01 1.00000000e+00]
 [1.00000000e+00 1.22464680e-16 6.12323400e-17 1.00000000e+00]]


In [156]:
print(rainbow)

['#8000ff', '#80ffb4', '#ff0000']
